In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')
!ls

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).
 changed.txt
 corpus.txt
 dumpfile.bz2
 enwiki-latest-pages-articles.xml.bz2
 glove.6B.zip
 pundata.csv
 Pun-GAN
 Pun-Generation
 semcor3.0.tar.gz
 semcor.py
 semeval2017_task7
 semeval2017_task7.tar.xz
'semeval2017_task7.tar.xz (Unzipped Files)'
 text
 wikiextractor


In [ ]:
path = '/content/gdrive/MyDrive/IE-643/enwiki-latest-pages-articles.xml.bz2'
%cd gdrive
%cd MyDrive
%cd IE-643
!ls

[Errno 2] No such file or directory: 'gdrive'
/content/gdrive/MyDrive/IE-643
[Errno 2] No such file or directory: 'MyDrive'
/content/gdrive/MyDrive/IE-643
[Errno 2] No such file or directory: 'IE-643'
/content/gdrive/MyDrive/IE-643
 changed.txt
 corpus.txt
 dumpfile.bz2
 enwiki-latest-pages-articles.xml.bz2
 glove.6B.zip
 pundata.csv
 Pun-GAN
 Pun-Generation
 semcor3.0.tar.gz
 semcor.py
 semeval2017_task7
 semeval2017_task7.tar.xz
'semeval2017_task7.tar.xz (Unzipped Files)'
 text
 wikiextractor


In [ ]:
!pip install wikiextractor

In [ ]:
! wikiextractor '/content/gdrive/MyDrive/IE-643/enwiki-latest-pages-articles.xml.bz2'  #extracting and cleaning the dumpfile for pre-processing

In [ ]:

import nltk
nltk.download('all')
import os
import glob
import re
from nltk import word_tokenize
from nltk import sent_tokenize
!pip install pywsd
#polysemes in homographic pun dataset
!pip install -U wn==0.0.23 #downgrading for pywsd(mentioned in the paper) to work
from nltk.corpus import wordnet as wn
from pywsd import disambiguate
from pywsd.similarity import max_similarity as maxsim

[nltk_data] Downloading collection 'all'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to /root/nltk_data...
[nltk_data]    |   Package abc is already up-to-date!
[nltk_data]    | Downloading package alpino to /root/nltk_data...
[nltk_data]    |   Package alpino is already up-to-date!
[nltk_data]    | Downloading package biocreative_ppi to
[nltk_data]    |     /root/nltk_data...
[nltk_data]    |   Package biocreative_ppi is already up-to-date!
[nltk_data]    | Downloading package brown to /root/nltk_data...
[nltk_data]    |   Package brown is already up-to-date!
[nltk_data]    | Downloading package brown_tei to /root/nltk_data...
[nltk_data]    |   Package brown_tei is already up-to-date!
[nltk_data]    | Downloading package cess_cat to /root/nltk_data...
[nltk_data]    |   Package cess_cat is already up-to-date!
[nltk_data]    | Downloading package cess_esp to /root/nltk_data...
[nltk_data]    |   Package cess_esp is already up-to-date!
[nltk_data]    | Downloading packag

In [ ]:
path = '/content/gdrive/MyDrive/IE-643/text'
path1 = '/content/gdrive/MyDrive/IE-643/corpus.txt'

import os
import glob

files = []
for filename in os.listdir(path):
  files.append(filename)
files
lang_text = []
raw = {}
files1 = []
with open(path1, 'a') as file_object:
  for filename in files:
    for file in os.listdir(os.path.join(path, filename)):
      with open(os.path.join(path, filename, file), 'rU') as f:
        raw[file] = f.read()



Pre-processing steps:
1. Corpus texts firstly lowercased and
tokenized, and all numeric characters are replaced
with “#”
2. We split the texts into sentences and
discard the sentences whose length is less than 5
words or more than 50 words
3. We then select polysemes appearing in the homographic pun data set
(Miller et al., 2017) and pun websites
4. Those polysemes in the corpus are replaced by the labeled
sense. We restrict that each sentence can be labeled with at most two polysemes in order to train
a reliable language model
5. If there are more polysemes in one sentence, we keep the last two because in our observation we found pun words tend
to occur near the end of a sentence.
6. After labeling, we keep the 105,000 most frequently occurring words and other words are replaced with the
'unk>' token. 
6.  We discard the sentences with
two or more 'unk>' tokens. There are totally
3,974 distinct labeled senses corresponding to a
total of 772 distinct polysemes.
7. While training the language model we use
2,595,435 sentences as the training set, and
741,551 sentences as the development set to decide when to stop training
8.  Since we hope to
generate a sentence containing the specified word
sense, we treat different senses of the same word
as independent new pseudo-words. We label the
senses of words with Word Sense Disambiguation (WSD) tools, and then we train the language
model using the corpus with labeled senses so
that for each word sense we can generate a sentence accordingly. We use the Python Implementations of WSD Technologies1 for WSD. This tool
can return the most possible sense for the target
word based on WordNet (Miller, 1995). We attach the sense label to the word and form a new
pseudo-word accordingly.

For training, first each word in the corpus is tagged with one word sense. Joint model is applicable during inference

In [ ]:
! git clone https://github.com/ArleneYuZhiwei/Pun-Generation

Cloning into 'Pun-Generation'...
remote: Enumerating objects: 39, done.
remote: Counting objects: 100% (39/39), done.
remote: Compressing objects: 100% (34/34), done.
remote: Total 120 (delta 13), reused 0 (delta 0), pack-reused 81
Receiving objects: 100% (120/120), 712.17 KiB | 3.14 MiB/s, done.
Resolving deltas: 100% (47/47), done.


In [ ]:
path = '/content/gdrive/MyDrive/IE-643/Pun-Generation/sem17_task7/test/subtask2-homographic-test.xml'
path2 = '/content/gdrive/MyDrive/IE-643/Pun-Generation/sem17_task7/test/subtask2-homographic-test.gold'


About the dataset

Semeval 2017-task7-subtask1

The dataset contains 2250 puns, where each word is annotated with 1 or 0, indicating a pun, or not pun

TODO- Extract two words and their senses


In [ ]:
import pandas as pd

pundata = pd.read_csv('/content/gdrive/MyDrive/IE-643/Pun-Generation/sem17_task7/test/pundata - pundata.csv')
pundata

Unnamed: 0  ...                             sense2
0              0  ...                     save%2:41:02::
1              1  ...                    sting%1:04:01::
2              2  ...  entrenched%5:00:00:established:00
3              3  ...                    forge%2:38:01::
4              4  ...                      hit%1:04:02::
...          ...  ...                                ...
1293        1293  ...                    waste%2:29:00::
1294        1294  ...                  battery%1:14:01::
1295        1295  ...                 play_out%2:36:00::
1296        1296  ...      bright%5:00:00:intelligent:00
1297        1297  ...              lame%5:00:01:unfit:01

[1298 rows x 5 columns]

In [ ]:
import glob
import re
m = '0'
n ='0'
pseudo1  = '0'
pseudo2 = '0'
def get_synset_from_id(word, sense1, sense2):
  global m, n, pseudo1, pseudo2
  x = wn.synsets(word)
  for i in range(len(x)):
    lemmas = x[i].lemmas()
    for j in range(len(lemmas)):
      if lemmas[j].key() == sense1:
        m = x[i]
        pseudo1 = str(m)
        pseudo1 = re.sub('[()]', '', pseudo1)
        pseudo1 = re.sub('[.]', '', pseudo1)
        pseudo1 = re.sub('Synset', '', pseudo1)
        pseudo1 = re.sub("[']", "", pseudo1)
      if lemmas[j].key() == sense2:
        n = x[i]
        pseudo2 = str(n)
        pseudo2 = re.sub('[()]', '', pseudo2)
        pseudo2 = re.sub('[.]', '', pseudo2)
        pseudo2 = re.sub('Synset', '', pseudo2)
        pseudo2 = re.sub("[']", "", pseudo2)
  return (pseudo1, m), (pseudo2, n)



In [ ]:
i=0
pun = {}
for index, row in pundata.iterrows():
  word = row['word']
  sense1 = row['sense1']
  sense2 = row['sense2']
  A= get_synset_from_id(word, sense1, sense2)
  print(A)
  pun[word] = A
  i = i+1

str(m)

(('savev04', Synset('save.v.04')), ('deliverv08', Synset('deliver.v.08')))
(('stingn03', Synset('sting.n.03')), ('deliverv08', Synset('deliver.v.08')))
(('entrencheds01', Synset('entrenched.s.01')), ('entrencheds02', Synset('entrenched.s.02')))
(('forgev01', Synset('forge.v.01')), ('forgev04', Synset('forge.v.04')))
(('hitn02', Synset('hit.n.02')), ('hitn03', Synset('hit.n.03')))
(('vaultn02', Synset('vault.n.02')), ('vaultn04', Synset('vault.n.04')))
(('deepa03', Synset('deep.a.03')), ('deeps02', Synset('deep.s.02')))
(('deepa03', Synset('deep.a.03')), ('pinv02', Synset('pin.v.02')))
(('solvev01', Synset('solve.v.01')), ('lapv04', Synset('lap.v.04')))
(('admitv01', Synset('admit.v.01')), ('admitv02', Synset('admit.v.02')))
(('crispenv01', Synset('crispen.v.01')), ('toastv02', Synset('toast.v.02')))
(('plantn01', Synset('plant.n.01')), ('plantn02', Synset('plant.n.02')))
(('squaren01', Synset('square.n.01')), ('squaren05', Synset('square.n.05')))
(('dangerouss02', Synset('dangerous.s.0

"Synset('feeble.s.01')"

In [ ]:
path = '/content/gdrive/MyDrive/IE-643/text'
path1 = '/content/gdrive/MyDrive/IE-643/corpus.txt'

import os
import glob

files = []
for filename in os.listdir(path):
  files.append(filename)
files
lang_text = []
raw = {}
files1 = []
with open(path1, 'a') as file_object:
  for filename in files:
    for file in os.listdir(os.path.join(path, filename)):
      with open(os.path.join(path, filename, file), 'rU') as f:
        textfile = f.read()
        break

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: 'U' mode is deprecated


In [ ]:
textfile

'<doc id="34272" url="?curid=34272" title="Yiddish">\nYiddish\n\nYiddish (, or , "yidish" or "idish", , ; in older sources , "Yidish-Taytsh", ) is a High German-derived language historically spoken by the Ashkenazi Jews. It originated during the 9th century in Central Europe, providing the nascent Ashkenazi community with a High German-based vernacular fused with elements taken from Hebrew and Aramaic, as well as Slavic languages and traces of Romance languages. Yiddish writing uses the Hebrew alphabet. , there were around 1.5–2\xa0million speakers of Yiddish, mostly Hasidic and Haredi Jews.\nThe earliest surviving references date from the 12th century and call the language ("loshn-ashknaz", "language of Ashkenaz") or ("taytsh"), a variant of "tiutsch", the contemporary name for Middle High German. Colloquially, the language is sometimes called ("mame-loshn", ), distinguishing it from ("loshn koydesh", "holy tongue"), meaning Hebrew and Aramaic. The term "Yiddish", short for "Yidish Ta

In [ ]:
pattern = '<[^,]+>'
clean = re.sub(pattern , '', textfile)
clean = re.sub("[0-9]", "#", clean)
lower = clean.lower()
split = sent_tokenize(lower)
split2 = []
for i in range(len(split)):
  x = word_tokenize(split[i])
  if len(x)>=5 and len(x)<= 50:
    split2.append(disambiguate(split[i]))

split2


[[('yiddish', Synset('yiddish.n.01')),
  ('yiddish', Synset('yiddish.n.01')),
  ('(', None),
  (',', None),
  ('or', None),
  (',', None),
  ('``', None),
  ('yidish', None),
  ("''", None),
  ('or', None),
  ('``', None),
  ('idish', None),
  ("''", None),
  (',', None),
  (',', None),
  (';', None),
  ('in', None),
  ('older', Synset('old.s.07')),
  ('sources', Synset('source.n.07')),
  (',', None),
  ('``', None),
  ('yidish-taytsh', None),
  ("''", None),
  (',', None),
  (')', None),
  ('is', None),
  ('a', None),
  ('high', Synset('high.s.07')),
  ('german-derived', None),
  ('language', Synset('terminology.n.01')),
  ('historically', Synset('historically.r.02')),
  ('spoken', Synset('speak.v.03')),
  ('by', None),
  ('the', None),
  ('ashkenazi', Synset('ashkenazi.n.01')),
  ('jews', Synset('jew.n.01')),
  ('.', None)],
 [('it', None),
  ('originated', Synset('originate.v.01')),
  ('during', None),
  ('the', None),
  ('#', None),
  ('th', Synset('thorium.n.01')),
  ('century', S

In [ ]:
path = '/content/gdrive/MyDrive/IE-643/changed.txt'
with open(path,'w+' ) as file_object:
  for pseudo in pun['waste']:
    for i in range(len(split2)): #sentence capture
      sen = i
      for j in range(len(split2[i])):#word capture
        wor = 0
        if str(split2[i][j][1]) ==  str(pseudo[0][1]):
          split2[i][j] = pseudo[0]
          wor = wor+1
          pos = j 
        if str(split2[i][j][1]) ==  str(pseudo[1][1]):
          split2[i][j] = pseudo[1]
          wor = wor+1
          pos = j 
          file_object.write(str('Sentence'+str(sen)+'word pos'+str(pos)+'No. of words changed'+str(wor)))

TypeError: ignored

In [ ]:
for pseudo in pun['waste']:
  print(pseudo[1])

Synset('waste.n.01')
[('waste', Synset('waste.n.05'))]
Synset('waste.v.10')
[('waste', Synset('waste.n.05'))]


LANGUAGE MODEL (generator)

We use the data set of
homographic puns from Miller et al. (2017). The
model is trained on the data set in asynchronous
forward/backward way. As the pun data set is
limited, the pun language model has no creativity,
which means if we input a word appearing in the
training data, then the output will usually be an existing sentence from the training data. Therefore,
we remove the sentences which contain words in
the 100 target words from the pun data set, and
then train the model for test.

Model specs:
I. The conditional language model for pun generation is similar to the seq2seq model with an input of only one word. We use Long Short-Term
Memory (LSTM) as encoder to map the input sequence (target word) to a vector of a fixed dimensionality, and then another LSTM network as decoder to decode the target sequence from the vector 


II. Our goal is to generate a sentence containing the target word. However, vanilla seq2seq model cannot guarantee the target word to appear in the generated sequence all the time. To
solve this problem, we adopt the asynchronous
forward/backward generation model

III. The model first generates the
backward sequence starting from the target word
wt at position t of the sentence (i.e., the words before wt), and ending up with “</s>” at the position 0 of the sentence. 

IV.. The model first generates the
backward sequence starting from the target word
wt at position t of the sentence (i.e., the words before wt), and ending up with “</s>” at the position 0 of the sentence



In [ ]:
import torch
from torch import rnn

In [ ]:
class BackwardModel(nn.Module):
    def __init__(self, dataset):
        super(Model, self).__init__()
        self.lstm_size = 2
        self.embedding_dim = 128
        self.num_layers = 3

        self.lstm = nn.LSTM(
            input_size=self.lstm_size,
            hidden_size=self.lstm_size,
            num_layers=self.num_layers,
            dropout=0.2,
        )

In [ ]:
def jointbeamsearchdecoder():
  for row in data:
    all_candidates = list()
    for i in range(len(sequences)):
      seq, score = sequences[i]
      for j in len(row):
        candidate =[seq+[j], score - log(row[j])]
        all_candidates.append(candidate)
    ordered = sorted(all_candidates, key = lambda, tup:tup[1] )
    sequences = ordered[:k]
  return sequences



hidden_state_1 #final hidden state of encoder
hidden_state_2 #final hidden state of decoder
b = 5
vocab_size = 10
Beam = {}
for i in range(b):
  Beam[i] = []
U_1_in = U_2_in = np.zeros(vocab_size)
BeamID = np.arange(b) #beam from which candidates came from
WordID = np.ones(b) #indices of candidatess in vocabulary
Outputs = []
t = 0
l = b
while l>0:
  o = []
  for i in range(b):
    #x[z] is word embedding corresponding to WordID[z]
    h_state_1 = lstm (x, hidden_state_1)
    h_state_2 = lstm(x, hidden_state_2)
    acc_score_1 = U_1_in + np.log(nn.softmax(h_state_1))
    acc_score_2 = U_2_in + np.log(nn.softmax(h_state_2))
    joint_score = acc_score_1 + acc_score_2
    o.append(joint_score)
    #select b best scores
    WordID = 
    BeamID = 
   for i in range(b):
     M = Beam[BeamID[i]]
     M.append(WordID[i])
     Beam[i] = M
     for i in range(vocab_size):
       U_1_in[i] = o[BeamID[i]][WordID[i]]
       U_1_in[i] = o[BeamID[i]][WordID[i]]
     if WordID[i] == 1:
       l = l-1
       Outputs.append(Beam[i]) 
     t = t + 1
return Outputs[0:b]


In [ ]:
!pip install xmlutils

  Created wheel for xmlutils: filename=xmlutils-1.4.1-cp36-none-any.whl size=10148 sha256=3ef50558bf1260f1a93e846f71ce25e80e22a2cadaf9d566cab0d77904c552dc
  Stored in directory: /root/.cache/pip/wheels/3f/ff/ed/5725817442d91550030e6bdbe1550223778a83974ab157d779
Successfully built xmlutils


In [ ]:
!xml2csv --input "/content/gdrive/MyDrive/IE-643/Pun-Generation/sem17_task7/test/subtask2-homographic-test.xml" --output "/content/gdrive/MyDrive/IE-643/Pun-Generation/subtask2-homographic-test.csv" --tag "word"

xml2csv
    --help for help

    


Wrote 1606 records to /content/gdrive/MyDrive/IE-643/Pun-Generation/subtask2-homographic-test.csv


In [ ]:
!ls

 corpus.txt
 dumpfile.bz2
 enwiki-latest-pages-articles.xml.bz2
 glove.6B.zip
 Pun-GAN
 Pun-Generation
 semcor3.0.tar.gz
 semcor.py
 semeval2017_task7
 semeval2017_task7.tar.xz
'semeval2017_task7.tar.xz (Unzipped Files)'
 text
 wikiextractor


In [ ]:
import xml.etree.ElementTree as ET
import csv
tree = ET.parse('/content/gdrive/MyDrive/IE-643/Pun-Generation/sem17_task7/test/subtask3-homographic-test.xml')
root = tree.getroot()

pundata1 = open('/content/gdrive/MyDrive/IE-643/pundata.csv', 'w', newline = '', encoding = 'utf-8')
csvwriter = csv.writer(pundata1)


In [ ]:
root

<Element 'corpus' at 0x7f634db6dc78>

In [ ]:
import xml.etree.ElementTree as ET
root = tree.getroot()

# one specific item attribute


print('Item #2 attribute:')
print(root[0][1].attrib)

# all item attributes
print('\nAll attributes:')
sub = []
text = []
for elem in root:
    for subelem in elem:
      if subelem.attrib['senses'] =='2':
        sub.append(subelem.attrib)
        text.append(subelem.text)

len(text)

Item #2 attribute:
{'id': 'hom_2_2', 'senses': '1'}

All attributes:


1298

In [ ]:
from nltk.corpus import wordnet as wn
wn.synset('take.v.01').lemmas()[0].key()

'take%2:41:04::'

In [ ]:
x = wn.synsets('chickened')
len(x)

0

In [ ]:
for i in range(len(x)):
  lemmas = x[i].lemmas()
  for j in range(len(lemmas)):
    if lemmas[j].key() == 'chicken%1:13:00::':
      print(x[i])
      print(x[i].definition())



Synset('chicken.n.01')
the flesh of a chicken used for food


In [ ]:
import pandas as pd

pundata = pd.read_csv('/content/gdrive/MyDrive/IE-643/Pun-Generation/sem17_task7/test/pundata - pundata.csv')
pundata

Unnamed: 0  ...                             sense2
0              0  ...                     save%2:41:02::
1              1  ...                    sting%1:04:01::
2              2  ...  entrenched%5:00:00:established:00
3              3  ...                    forge%2:38:01::
4              4  ...                      hit%1:04:02::
...          ...  ...                                ...
1293        1293  ...                    waste%2:29:00::
1294        1294  ...                  battery%1:14:01::
1295        1295  ...                 play_out%2:36:00::
1296        1296  ...      bright%5:00:00:intelligent:00
1297        1297  ...              lame%5:00:01:unfit:01

[1298 rows x 5 columns]

In [ ]:
import glob
import re
m = '0'
n ='0'
pseudo1  = '0'
pseudo2 = '0'
def get_synset_from_id(word, sense1, sense2):
  global m, n, pseudo1, pseudo2
  x = wn.synsets(word)
  for i in range(len(x)):
    lemmas = x[i].lemmas()
    for j in range(len(lemmas)):
      if lemmas[j].key() == sense1:
        m = x[i]
        pseudo1 = str(m)
        pseudo1 = re.sub('[()]', '', pseudo1)
        pseudo1 = re.sub('[.]', '', pseudo1)
        pseudo1 = re.sub('Synset', '', pseudo1)
        pseudo1 = re.sub("[']", "", pseudo1)
      if lemmas[j].key() == sense2:
        n = x[i]
        pseudo2 = str(n)
        pseudo2 = re.sub('[()]', '', pseudo2)
        pseudo2 = re.sub('[.]', '', pseudo2)
        pseudo2 = re.sub('Synset', '', pseudo2)
        pseudo2 = re.sub("[']", "", pseudo2)
  return (pseudo1, m), (pseudo2, n)



Creating the list of the pun words, and their sense keys to look up and retrieve

In [ ]:
i=0
pun = {}
for index, row in pundata.iterrows():
  word = row['word']
  sense1 = row['sense1']
  sense2 = row['sense2']
  A= get_synset_from_id(word, sense1, sense2)
  print(A)
  pun[word] = A
  i = i+1

str(m)

(('savev04', Synset('save.v.04')), ('deliverv08', Synset('deliver.v.08')))
(('stingn03', Synset('sting.n.03')), ('deliverv08', Synset('deliver.v.08')))
(('entrencheds01', Synset('entrenched.s.01')), ('entrencheds02', Synset('entrenched.s.02')))
(('forgev01', Synset('forge.v.01')), ('forgev04', Synset('forge.v.04')))
(('hitn02', Synset('hit.n.02')), ('hitn03', Synset('hit.n.03')))
(('vaultn02', Synset('vault.n.02')), ('vaultn04', Synset('vault.n.04')))
(('deepa03', Synset('deep.a.03')), ('deeps02', Synset('deep.s.02')))
(('deepa03', Synset('deep.a.03')), ('pinv02', Synset('pin.v.02')))
(('solvev01', Synset('solve.v.01')), ('lapv04', Synset('lap.v.04')))
(('admitv01', Synset('admit.v.01')), ('admitv02', Synset('admit.v.02')))
(('crispenv01', Synset('crispen.v.01')), ('toastv02', Synset('toast.v.02')))
(('plantn01', Synset('plant.n.01')), ('plantn02', Synset('plant.n.02')))
(('squaren01', Synset('square.n.01')), ('squaren05', Synset('square.n.05')))
(('dangerouss02', Synset('dangerous.s.0

"Synset('feeble.s.01')"

In [ ]:
import pandas as pd

pundata = pd.read_csv('/content/gdrive/MyDrive/IE-643/Pun-Generation/sem17_task7/test/pundata.csv')
pundata

Unnamed: 0  ...                             sense2
0              0  ...                     save%2:41:02::
1              1  ...                    sting%1:04:01::
2              2  ...  entrenched%5:00:00:established:00
3              3  ...                    forge%2:38:01::
4              4  ...                      hit%1:04:02::
...          ...  ...                                ...
1293        1293  ...                    waste%2:29:00::
1294        1294  ...                  battery%1:14:01::
1295        1295  ...                 play_out%2:36:00::
1296        1296  ...      bright%5:00:00:intelligent:00
1297        1297  ...              lame%5:00:01:unfit:01

[1298 rows x 5 columns]

In [ ]:
get_synset_from_id('count', 'count%2:32:00::', 'count%2:31:02::')

((Synset('count.v.01'), "'countv01'"), (Synset('count.v.08'), "'countv08'"))

In [ ]:
x = pd.DataFrame.from_dict(sub)
g = x['id']
text['id'] = g

0           hom_2_9
1           hom_3_7
2           hom_4_5
3          hom_5_15
4          hom_7_14
           ...     
1293     hom_2244_9
1294    hom_2245_10
1295     hom_2248_8
1296    hom_2249_13
1297     hom_2250_8
Name: id, Length: 1298, dtype: object

In [ ]:
wn.synset('count.v.08').definition()

'have faith or confidence in'

In [ ]:
!pip install pywsd
!pip install -U wn==0.0.23 #downgrading for pywsd(mentioned in the paper) to work
from nltk.corpus import wordnet as wn
from pywsd import disambiguate
from pywsd.similarity import max_similarity as maxsim

Processing /root/.cache/pip/wheels/56/e3/c4/886021dbf4d758dc3cb9ddaa47d7d6fc895240d83f010e6305/wn-0.0.23-cp36-none-any.whl
  Found existing installation: wn 0.3.0
    Uninstalling wn-0.3.0:
      Successfully uninstalled wn-0.3.0


Warming up PyWSD (takes ~10 secs)... took 3.4034454822540283 secs.


In [ ]:
a

[('Sorry', Synset('regretful.a.01')),
 (',', None),
 ('I', None),
 ('can', None),
 ('not', None),
 ('count', Synset('reckon.v.06')),
 ('on', None),
 ('you', None)]

In [ ]:
path = '/content/gdrive/MyDrive/IE-643/text'
path1 = '/content/gdrive/MyDrive/IE-643/corpus.txt'

import os
import glob

files = []
for filename in os.listdir(path):
  files.append(filename)
files
lang_text = []
raw = {}
files1 = []
with open(path1, 'a') as file_object:
  for filename in files:
    for file in os.listdir(os.path.join(path, filename)):
      with open(os.path.join(path, filename, file), 'rU') as f:
        textfile = f.read()
        break

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:17: DeprecationWarning: 'U' mode is deprecated


In [ ]:
textfile

'<doc id="34272" url="?curid=34272" title="Yiddish">\nYiddish\n\nYiddish (, or , "yidish" or "idish", , ; in older sources , "Yidish-Taytsh", ) is a High German-derived language historically spoken by the Ashkenazi Jews. It originated during the 9th century in Central Europe, providing the nascent Ashkenazi community with a High German-based vernacular fused with elements taken from Hebrew and Aramaic, as well as Slavic languages and traces of Romance languages. Yiddish writing uses the Hebrew alphabet. , there were around 1.5–2\xa0million speakers of Yiddish, mostly Hasidic and Haredi Jews.\nThe earliest surviving references date from the 12th century and call the language ("loshn-ashknaz", "language of Ashkenaz") or ("taytsh"), a variant of "tiutsch", the contemporary name for Middle High German. Colloquially, the language is sometimes called ("mame-loshn", ), distinguishing it from ("loshn koydesh", "holy tongue"), meaning Hebrew and Aramaic. The term "Yiddish", short for "Yidish Ta

In [ ]:
pattern = '<[^,]+>'
clean = re.sub(pattern , '', textfile)
clean = re.sub("[0-9]", "#", clean)
lower = clean.lower()
split = sent_tokenize(lower)
split2 = []
for i in range(len(split)):
  x = word_tokenize(split[i])
  if len(x)>=5 and len(x)<= 50:
    split2.append(disambiguate(split[i]))

split2


[[('yiddish', Synset('yiddish.n.01')),
  ('yiddish', Synset('yiddish.n.01')),
  ('(', None),
  (',', None),
  ('or', None),
  (',', None),
  ('``', None),
  ('yidish', None),
  ("''", None),
  ('or', None),
  ('``', None),
  ('idish', None),
  ("''", None),
  (',', None),
  (',', None),
  (';', None),
  ('in', None),
  ('older', Synset('old.s.07')),
  ('sources', Synset('source.n.07')),
  (',', None),
  ('``', None),
  ('yidish-taytsh', None),
  ("''", None),
  (',', None),
  (')', None),
  ('is', None),
  ('a', None),
  ('high', Synset('high.s.07')),
  ('german-derived', None),
  ('language', Synset('terminology.n.01')),
  ('historically', Synset('historically.r.02')),
  ('spoken', Synset('speak.v.03')),
  ('by', None),
  ('the', None),
  ('ashkenazi', Synset('ashkenazi.n.01')),
  ('jews', Synset('jew.n.01')),
  ('.', None)],
 [('it', None),
  ('originated', Synset('originate.v.01')),
  ('during', None),
  ('the', None),
  ('#', None),
  ('th', Synset('thorium.n.01')),
  ('century', S

In [ ]:
wn.synset('count.v.07').definition()

'have a certain value or carry a certain weight'

In [ ]:
get_synset_from_id('count', 'count%2:32:00::', 'count%2:31:02::')

((Synset('count.v.01'), "'countv01'"), (Synset('count.v.08'), "'countv08'"))

In [ ]:
split = sent_tokenize(lower)
print(split)
split2 =[]
for i in range(len(split)):
  x = word_tokenize(split[i])
  if len(x)>=5 and len(x)<= 50:
    split2.append(split[i])

len

['\nyiddish\n\nyiddish (, or , "yidish" or "idish", , ; in older sources , "yidish-taytsh", ) is a high german-derived language historically spoken by the ashkenazi jews.', 'it originated during the #th century in central europe, providing the nascent ashkenazi community with a high german-based vernacular fused with elements taken from hebrew and aramaic, as well as slavic languages and traces of romance languages.', 'yiddish writing uses the hebrew alphabet.', ', there were around #.#–#\xa0million speakers of yiddish, mostly hasidic and haredi jews.', 'the earliest surviving references date from the ##th century and call the language ("loshn-ashknaz", "language of ashkenaz") or ("taytsh"), a variant of "tiutsch", the contemporary name for middle high german.', 'colloquially, the language is sometimes called ("mame-loshn", ), distinguishing it from ("loshn koydesh", "holy tongue"), meaning hebrew and aramaic.', 'the term "yiddish", short for "yidish taitsh" ("jewish german"), did not 

<function len>

In [ ]:
split2[0][1]

('yiddish', Synset('yiddish.n.01'))

In [ ]:
split2

[[('yiddish', Synset('yiddish.n.01')),
  ('yiddish', Synset('yiddish.n.01')),
  ('wastev10', Synset('waste.v.10')),
  (',', None),
  ('or', None),
  (',', None),
  ('``', None),
  ('yidish', None),
  ("''", None),
  ('or', None),
  ('``', None),
  ('idish', None),
  ("''", None),
  (',', None),
  (',', None),
  (';', None),
  ('in', None),
  ('older', Synset('old.s.07')),
  ('sources', Synset('source.n.07')),
  (',', None),
  ('``', None),
  ('yidish-taytsh', None),
  ("''", None),
  (',', None),
  (')', None),
  ('is', None),
  ('a', None),
  ('high', Synset('high.s.07')),
  ('german-derived', None),
  ('language', Synset('terminology.n.01')),
  ('historically', Synset('historically.r.02')),
  ('spoken', Synset('speak.v.03')),
  ('by', None),
  ('the', None),
  ('ashkenazi', Synset('ashkenazi.n.01')),
  ('jews', Synset('jew.n.01')),
  ('.', None)],
 [('it', None),
  ('originated', Synset('originate.v.01')),
  ('during', None),
  ('the', None),
  ('#', None),
  ('th', Synset('thorium.n

In [ ]:
path = '/content/gdrive/MyDrive/IE-643/changed.txt'
with open(path,'w+' ) as file_object:
  for pseudo in pun['waste']:
    for i in range(len(split2)): #sentence capture
      sen = i
      for j in range(len(split2[i])):#word capture
        wor = 0
        if str(split2[i][j][1]) ==  str(pseudo[0][1]):
          split2[i][j] = pseudo[0]
          wor = wor+1
          pos = j 
        if str(split2[i][j][1]) ==  str(pseudo[1][1]):
          split2[i][j] = pseudo[1]
          wor = wor+1
          pos = j 
          file_object.write(str('Sentence'+str(sen)+'word pos'+str(pos)+'No. of words changed'+str(wor)))

In [ ]:
pun['waste']

(('wasten01', Synset('waste.n.01')), ('wastev10', Synset('waste.v.10')))